In [3]:

import os
import sys

%run 'get_subject_data.ipynb'
%run 'Preprocess_data.ipynb'

range_file_path = f'./resources/variable_ranges.csv'
SUBJECT_FOLDER_PATH = f'./data/'


var_map = read_itemid_to_variable_map(f'./resources/itemid_to_variable_map.csv')
variables = var_map.VARIABLE.unique()

for subject_dir in os.listdir(SUBJECT_FOLDER_PATH):
    dn = os.path.join(SUBJECT_FOLDER_PATH, subject_dir)
    dn
    try:
        subject_id = int(subject_dir)
        if not os.path.isdir(dn):
            raise Exception
    except:
        continue
    sys.stdout.write('Subject {}: '.format(subject_id))
    sys.stdout.flush()

    try:
        sys.stdout.write('reading...')
        sys.stdout.flush()
        stays = read_stays(os.path.join(SUBJECT_FOLDER_PATH, subject_dir))
        diagnoses = read_diagnoses(os.path.join(SUBJECT_FOLDER_PATH, subject_dir))
        events = read_events(os.path.join(SUBJECT_FOLDER_PATH, subject_dir))
    except:
        sys.stdout.write('error reading from disk:\n')
        continue
    else:
        sys.stdout.write('got {0} stays, {1} diagnoses, {2} events...'.format(stays.shape[0], diagnoses.shape[0], events.shape[0]))
        sys.stdout.flush()

    episodic_data = assemble_episodic_data(stays, diagnoses)

    sys.stdout.write('cleaning and converting to time series...')
    sys.stdout.flush()
    events = map_itemids_to_variables(events, var_map)
    events = clean_events(events)
    if events.shape[0] == 0:
        sys.stdout.write('no valid events!\n')
        continue
    timeseries = convert_events_to_timeseries(events, variables=variables)
    
    sys.stdout.write('extracting separate episodes...')
    sys.stdout.flush()

    for i in range(stays.shape[0]):
        stay_id = stays.ICUSTAY_ID.iloc[i]
        sys.stdout.write(' {}'.format(stay_id))
        sys.stdout.flush()
        intime = stays.INTIME.iloc[i]
        outtime = stays.OUTTIME.iloc[i]

        episode = get_events_for_stay(timeseries, stay_id, intime, outtime)
        if episode.shape[0] == 0:
            sys.stdout.write(' (no data!)')
            sys.stdout.flush()
            continue

        episode = add_hours_elpased_to_events(episode, intime).set_index('HOURS').sort_index(axis=0)
        episodic_data.Weight.loc[stay_id] = get_first_valid_from_timeseries(episode, 'Weight')
        episodic_data.Height.loc[stay_id] = get_first_valid_from_timeseries(episode, 'Height')
        episodic_data.loc[episodic_data.index==stay_id].to_csv(os.path.join(SUBJECT_FOLDER_PATH, subject_dir, 'episode{}.csv'.format(i+1)), index_label='Icustay')
        columns = list(episode.columns)
        columns_sorted = sorted(columns, key=(lambda x: "" if x == "Hours" else x))
        episode = episode[columns_sorted]
        episode.to_csv(os.path.join(SUBJECT_FOLDER_PATH, subject_dir, 'episode{}_timeseries.csv'.format(i+1)), index_label='Hours')
    sys.stdout.write(' DONE!\n')


Subject 49138: reading...got 1 stays, 14 diagnoses, 684 events...cleaning and converting to time series...extracting separate episodes... 296225

/home/andreass2/.local/lib/python3.6/site-packages/pandas/core/indexing.py:194: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)
/home/andreass2/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:163: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/home/andreass2/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:155: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


 DONE!
Subject 31346: reading...got 1 stays, 2 diagnoses, 3 events...cleaning and converting to time series...no valid events!
Subject 5502: reading...got 1 stays, 9 diagnoses, 449 events...cleaning and converting to time series...extracting separate episodes... 238544 DONE!
Subject 1662: reading...got 1 stays, 9 diagnoses, 130 events...cleaning and converting to time series...extracting separate episodes... 207701 DONE!
Subject 66505: reading...got 1 stays, 21 diagnoses, 176 events...cleaning and converting to time series...extracting separate episodes... 264236 DONE!
Subject 89084: reading...got 1 stays, 10 diagnoses, 245 events...cleaning and converting to time series...extracting separate episodes... 274709 DONE!
Subject 22518: reading...got 1 stays, 8 diagnoses, 799 events...cleaning and converting to time series...extracting separate episodes... 299349 DONE!
Subject 23613: reading...got 2 stays, 26 diagnoses, 191 events...cleaning and converting to time series...extracting separa

/home/andreass2/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:38: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


got 1 stays, 32 diagnoses, 944 events...cleaning and converting to time series...extracting separate episodes... 265157 DONE!
Subject 60575: reading...got 1 stays, 18 diagnoses, 323 events...cleaning and converting to time series...extracting separate episodes... 266564 DONE!
Subject 78505: reading...got 1 stays, 10 diagnoses, 211 events...cleaning and converting to time series...extracting separate episodes... 231377 DONE!
Subject 10875: reading...got 1 stays, 3 diagnoses, 183 events...cleaning and converting to time series...extracting separate episodes... 276672 DONE!
Subject 21458: reading...got 2 stays, 18 diagnoses, 505 events...cleaning and converting to time series...extracting separate episodes... 298645 259604 DONE!
Subject 97818: reading...got 1 stays, 10 diagnoses, 115 events...cleaning and converting to time series...extracting separate episodes... 249170 DONE!
Subject 99165: reading...got 1 stays, 15 diagnoses, 254 events...cleaning and converting to time series...extract

...

Subject 29280: reading...got 2 stays, 19 diagnoses, 61 events...cleaning and converting to time series...extracting separate episodes... 242759 (no data!) 222084 DONE!
Subject 14902: reading...got 1 stays, 3 diagnoses, 28 events...cleaning and converting to time series...no valid events!
Subject 43417: reading...got 1 stays, 21 diagnoses, 631 events...cleaning and converting to time series...extracting separate episodes... 251349 DONE!
Subject 10842: reading...got 1 stays, 12 diagnoses, 237 events...cleaning and converting to time series...extracting separate episodes... 262617 DONE!
Subject 10846: reading...got 1 stays, 7 diagnoses, 105 events...cleaning and converting to time series...no valid events!
Subject 6565: reading...got 1 stays, 6 diagnoses, 20 events...cleaning and converting to time series...no valid events!
Subject 18618: reading...got 1 stays, 7 diagnoses, 687 events...cleaning and converting to time series...extracting separate episodes... 253275 DONE!
Subject 14870: re

Subject 65179: reading...got 1 stays, 10 diagnoses, 147 events...cleaning and converting to time series...extracting separate episodes... 204025 DONE!
Subject 78: reading...got 1 stays, 8 diagnoses, 145 events...cleaning and converting to time series...extracting separate episodes... 233150 DONE!
Subject 49225: reading...got 1 stays, 13 diagnoses, 230 events...cleaning and converting to time series...extracting separate episodes... 224174 DONE!
Subject 60219: reading...got 1 stays, 9 diagnoses, 207 events...cleaning and converting to time series...extracting separate episodes... 219023 DONE!
Subject 63571: reading...got 1 stays, 8 diagnoses, 197 events...cleaning and converting to time series...extracting separate episodes... 265110 DONE!
Subject 18215: reading...got 1 stays, 11 diagnoses, 529 events...cleaning and converting to time series...extracting separate episodes... 260265 DONE!
Subject 7506: reading...got 1 stays, 11 diagnoses, 199 events...cleaning and converting to time seri

/home/andreass2/.local/lib/python3.6/site-packages/pandas/core/generic.py:3643: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[name] = value


extracting separate episodes... 207753 DONE!
Subject 14895: reading...got 1 stays, 3 diagnoses, 3 events...cleaning and converting to time series...no valid events!
Subject 30501: reading...got 2 stays, 34 diagnoses, 442 events...cleaning and converting to time series...extracting separate episodes... 295981 204208 DONE!
Subject 23535: reading...got 1 stays, 17 diagnoses, 688 events...cleaning and converting to time series...extracting separate episodes... 261259 DONE!
Subject 89483: reading...got 1 stays, 27 diagnoses, 215 events...cleaning and converting to time series...extracting separate episodes... 235216 DONE!
Subject 10920: reading...got 1 stays, 9 diagnoses, 613 events...cleaning and converting to time series...extracting separate episodes... 204892 DONE!
Subject 29869: reading...got 1 stays, 8 diagnoses, 249 events...cleaning and converting to time series...extracting separate episodes... 288802 DONE!
Subject 16552: reading...got 1 stays, 8 diagnoses, 1415 events...cleaning a

KeyboardInterrupt: 